#ALGORITHMIC TRADING STRATEGY FOR BTC/USDT

###Importing the libraries

In [ ]:
import pandas as pd
import matplotlib.pyplot as plt
import seaborn as sns
import warnings
warnings.filterwarnings("ignore")

In [ ]:
pip install dash dash-core-components dash-html-components plotly pandas

In [ ]:
df = pd.read_csv("/content/btc_4h.csv")

#**Data Visualization**

In [ ]:
pip install pandas plotly

In [ ]:
df.set_index('datetime', inplace=True)

###**1. Equity curve**

The equity curve over time to visualize the cumulative returns of your trading strategy. This will give you a clear picture of how your strategy performs compared to a simple buy and hold strategy.

In [ ]:
import plotly.express as px

df['equity_curve'] = (1 + df['Strategy_returns']).cumprod()

fig = px.line(df, x=df.index, y='equity_curve', title='Equity Curve Over Time')
fig.update_xaxes(title_text='Date')
fig.update_yaxes(title_text='Equity Curve')

fig.show()

1. The starting point of each curve: This will tell you how much each strategy was initially invested with.


2. The overall slope of each curve: A steeper upward slope indicates better performance.


3. The drawdowns of each curve: A drawdown is a decline in the value of the portfolio from a previous peak. The depth and frequency of drawdowns can indicate the level of risk associated with each strategy.


4. The ending point of each curve: This will tell you the final value of each portfolio.
Portfolio" here refers specifically to the collection of assets held by the trading strategy you're analyzing. It encompasses all the investments and positions taken on by the strategy at any given point in time.

###**2. Rolling Statistics**

Rolling statistics such as rolling mean and rolling standard deviation of the predicted strategy returns can help you identify periods of high volatility or mean-reverting behavior.

In [ ]:
import plotly.graph_objects as go
window_size = 13
trace_rolling_mean = go.Scatter(x=df.index, y=df['rolling_mean'], mode='lines', name='Rolling Mean')
trace_rolling_std_upper = go.Scatter(x=df.index, y=df['rolling_mean'] + 2 * df['rolling_std'],
                                    mode='lines', name='Upper Bound (Mean + 2*Std)', line=dict(dash='dash'))
trace_rolling_std_lower = go.Scatter(x=df.index, y=df['rolling_mean'] - 2 * df['rolling_std'],
                                    mode='lines', name='Lower Bound (Mean - 2*Std)', line=dict(dash='dash'))

data = [trace_rolling_mean, trace_rolling_std_upper, trace_rolling_std_lower]

layout = go.Layout(title=f'Rolling Mean and Std (Window Size: {window_size})',
                   xaxis=dict(title='Date'), yaxis=dict(title='Value'))

fig = go.Figure(data=data, layout=layout)
fig.show()


1. Rolling Mean (blue line): This line tracks the average return of the strategy over a moving window of time (13 days in this case). It smooths out short-term fluctuations and reveals underlying trends.


2. Upper Bound (orange line): Calculated as the rolling mean plus 2 standard deviations. It indicates periods of unusually high returns, potentially signaling high volatility or outlier events.


3. Lower Bound (green line): Calculated as the rolling mean minus 2 standard deviations. It highlights periods of unusually low returns, potentially indicating mean-reverting behavior or periods of market stress.


**Interpreting Volatility and Mean Reversion:**

* Widening gaps between the rolling mean and the bounds: Suggest periods of heightened volatility, meaning the strategy's returns are experiencing larger swings than usual.


* Rolling mean crossing or touching the bounds: Indicate potential shifts in market behavior or strategy performance.


 * Rolling mean consistently reverting back towards the center: Suggest mean-reverting behavior, meaning the strategy tends to recover from periods of extreme returns.

###**3. Drawdown**

Visualize drawdowns in the equity curve. This will help you understand the risk and potential losses associated with the strategy.

In [ ]:
equity_curve = (1 + df['Strategy_returns']).cumprod()

peak = equity_curve.expanding().max()
drawdown = (equity_curve - peak) / peak

trace_equity_curve = go.Scatter(x=df.index, y=equity_curve, mode='lines', name='Equity Curve')
trace_drawdown = go.Scatter(x=df.index, y=drawdown, mode='lines', name='Drawdown', fill='tozeroy', line=dict(color='red'))

data = [trace_equity_curve, trace_drawdown]


layout = go.Layout(title='Equity Curve and Drawdowns',
                   xaxis=dict(title='Date'), yaxis=dict(title='Value'))

fig = go.Figure(data=data, layout=layout)
fig.show()

1. Equity Curve: The primary line on the graph, tracking the cumulative value of your trading strategy's portfolio over time. It illustrates the overall performance of the strategy.


2. Drawdown Line: A secondary line, typically below the equity curve, indicating periods of decline in portfolio value from previous peaks. It highlights the extent of losses experienced during these periods.


**Interpreting Drawdowns:**

* Depth of Drawdowns: The vertical distance between the equity curve's peak and the drawdown line represents the percentage of value lost during that period. Deeper drawdowns indicate higher risk and potential for significant losses.


* Frequency of Drawdowns: The number of drawdowns within a given timeframe signifies the strategy's volatility. More frequent drawdowns suggest greater instability and potential for frequent losses.


* Duration of Drawdowns: The length of time a drawdown lasts before recovery indicates the strategy's resilience. Prolonged drawdowns can test investor patience and potentially lead to premature exits.

###**4.Performance Metrics:**

Display key performance metrics such as Sharpe ratio, maximum drawdown, and total profit/loss. This will provide a quantitative assessment of the strategy's risk-adjusted returns.

In [ ]:
equity_curve = df['equity_curve']
log_returns = df['Log_returns']

total_profit_loss = equity_curve.iloc[-1] - equity_curve.iloc[0]
returns = equity_curve.pct_change().dropna()
sharpe_ratio = np.sqrt(252) * np.mean(returns) / np.std(returns)
drawdown = (equity_curve - equity_curve.cummax()) / equity_curve.cummax()
max_drawdown = drawdown.min()

print(f"Total Profit/Loss: {total_profit_loss:.2f}")
print(f"Sharpe Ratio: {sharpe_ratio:.4f}")
print(f"Maximum Drawdown: {max_drawdown:.4f}")


Total Profit/Loss: 20.81
Sharpe Ratio: 0.6245
Maximum Drawdown: -0.9591


###**5. Histogram of Returns**

Histogram of the strategy returns is to understand the distribution of returns. This can provide insights into the strategy's risk profile.

In [ ]:
strategy_returns = df['Strategy_returns']

fig = px.histogram(df, x=strategy_returns, nbins=50, marginal="rug",
                   labels={'value': 'Returns', 'count': 'Frequency'},
                   title='Histogram of Strategy Returns')
fig.show()

**Interpreting the Histogram:**

**Shape:**

 * Symmetrical: Even distribution around a central peak suggests a balanced risk profile, with similar chances of positive and negative returns of similar magnitudes.


* Skewed: More weight on one side indicates a tendency for certain types of returns (positive or negative).


* Peakedness (Kurtosis): High peaks suggest frequent returns close to the average, while flatter histograms indicate a wider range of outcomes.


* Center: The peak's location (center of distribution) represents the most common return level.


* Spread: The width of the distribution indicates variability in returns. Wide ranges suggest higher volatility and potential for extreme outcomes.


**Risk Insights from the Histogram:**

* Concentration: Tall bars in a narrow range suggest a more predictable strategy with concentrated returns.


* Dispersion: Bars spread across a wide range indicate a higher probability of unexpected outcomes, both positive and negative.


* Tails: The presence of significant bars in extreme ranges (far left or right tails) suggests potential for large gains or losses, signaling higher risk.

###**6. Trade Analysis**

This will help you analyze the effectiveness of your entry and exit signals.

In [ ]:
buy_signals = df[df['Buy'].notnull()]
sell_signals = df[df['Sell'].notnull()]

fig = px.scatter(df, x=df.index, y='close', title='Trade Analysis - Buy and Sell Signals', labels={'close': 'Close Price'})

fig.add_trace(go.Scatter(x=buy_signals.index, y=buy_signals['Buy'], mode='markers', name='Buy Signal', marker=dict(color='green', symbol='triangle-up', size=10)))

fig.add_trace(go.Scatter(x=sell_signals.index, y=sell_signals['Sell'], mode='markers', name='Sell Signal', marker=dict(color='red', symbol='triangle-down', size=10)))

fig.update_xaxes(title_text='Date')
fig.update_yaxes(title_text='Close Price')

fig.show()

###**7. Correlation Heatmap**

 This heatmap is to visualize the correlation between different features used in the model. This can help you identify multicollinearity issues.

In [ ]:
features = ['open', 'high', 'low', 'close', 'volume', 'SMA', 'Simple_returns', 'Log_returns', 'ratios', 'positions', 'Buy', 'Sell', 'Strategy_returns', 'rolling_mean', 'rolling_std', 'z_score', 'Predicted_Strategy_Returns']
correlation_matrix = df[features].corr()

fig = go.Figure(data=go.Heatmap(
    z=correlation_matrix.values,
    x=features,
    y=features,
    colorscale='Viridis',
    colorbar=dict(title='Correlation'),
))

fig.update_layout(title='Correlation Heatmap', width=800, height=700)
fig.show()

##Feature Engineering and Data Cleaning

In [ ]:
for column in df.columns:

    fig = go.Figure()
    fig.add_trace(go.Box(y=df[column], name=column))

    fig.update_layout(title=f'Boxplot of {column}',
                      xaxis=dict(title=column),
                      yaxis=dict(title='Values'))
    fig.show()

In [ ]:
Q3 = df['volume'].quantile(q=0.75)
Q1 = df['volume'].quantile(q=0.25)
IQR = Q3 - Q1
up = Q3 + 1.5 * IQR
down = Q1 - 1.5 * IQR

import numpy as np

def cap_extreme_values(data, lower_bound, upper_bound):
    capped_data = np.clip(data, lower_bound, upper_bound)
    return capped_data

a = cap_extreme_values(df['volume'], down, up)
df['volume'] = a

###**Mean reversion Strategy**

In [ ]:
def SMA(data,period=30,column=['close']):
  return df[column].rolling(window=period).mean()

In [ ]:
df['SMA'] = SMA(df,21)
df['Simple_returns']=df.pct_change(1)['close']
df['Log_returns']=np.log(1+df['Simple_returns'])
df['ratios'] = df['close']/df['Simple_returns']

In [ ]:
df['ratios'].describe()

count    8.930000e+03
mean              inf
std               NaN
min     -8.786593e+09
25%     -2.145003e+06
50%      2.078527e+05
75%      2.244540e+06
max               inf
Name: ratios, dtype: float64

In [ ]:
columns_to_fill = ['SMA', 'Simple_returns', 'Log_returns', 'ratios']
df[columns_to_fill] = df[columns_to_fill].fillna(method='bfill')

In [ ]:
percentiles = [15,20,50,80,85]
ratios=df['ratios']
percentile_values = np.percentile(ratios,percentiles)
percentile_values

array([-4569481.37293745, -3072917.04045618,   207931.65456576,
        3168243.14871754,  4666084.27332086])

In [ ]:
fig = px.line(df, x=df.index, y='ratios', title='Ratios')
fig.update_xaxes(title_text='Date')
fig.update_yaxes(title_text='Ratios')
fig.show()

In [ ]:
sell = percentile_values[-1]
buy = percentile_values[0]

df['positions'] = np.where(df.ratios>sell,0,np.nan)
df['positions'] = np.where(df.ratios<buy,1,df['positions'])

df['Buy'] = np.where(df['positions']==1,df['close'],np.nan)
df['Sell'] = np.where(df['positions']==0,df['close'],np.nan)

In [ ]:

fig = go.Figure()
fig.add_trace(go.Scatter(x=df.index, y=df['close'], mode='lines', name='Close Price', line=dict(color='blue')))
fig.add_trace(go.Scatter(x=df.index, y=df['SMA'], mode='lines', name='SMA', line=dict(color='orange')))
fig.add_trace(go.Scatter(x=df[df['Buy'].notnull()].index, y=df[df['Buy'].notnull()]['Buy'],
                         mode='markers', name='Buy Signal', marker=dict(color='green', symbol='triangle-up')))
fig.add_trace(go.Scatter(x=df[df['Sell'].notnull()].index, y=df[df['Sell'].notnull()]['Sell'],
                         mode='markers', name='Sell Signal', marker=dict(color='red', symbol='triangle-down')))

fig.update_layout(title='Close w/ Buy and Sell Signals',
                  xaxis=dict(title='Date'),
                  yaxis=dict(title='Close Price'),
                  legend=dict(orientation='h', yanchor='bottom', y=1.02, xanchor='right', x=1),
                  showlegend=True)
fig.show()

In [ ]:
df.columns

Index(['open', 'high', 'low', 'close', 'volume', 'SMA', 'Simple_returns',
       'Log_returns', 'ratios', 'positions', 'Buy', 'Sell'],
      dtype='object')

In [ ]:
df['Strategy_returns'] = df.positions.shift(1)*df.Log_returns

In [ ]:
columns_to_interpolate = ['positions', 'Buy', 'Sell', 'Strategy_returns']

df[columns_to_interpolate] = df[columns_to_interpolate].interpolate()

In [ ]:
df[columns_to_interpolate] = df[columns_to_interpolate].fillna(method='ffill')

In [ ]:
df.fillna(0, inplace=True)

In [ ]:
df['Strategy_returns'] = pd.to_numeric(df['Strategy_returns'], errors='coerce')

In [ ]:
fig = go.Figure()
buy_hold_returns = np.exp(df['Log_returns'].dropna()).cumprod()
mean_reversion_returns = np.exp(df['Strategy_returns'].dropna()).cumprod()

fig.add_trace(go.Scatter(x=df.index, y=buy_hold_returns, mode='lines', name='Buy/Hold strategy', line=dict(color='green')))

fig.add_trace(go.Scatter(x=df.index, y=mean_reversion_returns, mode='lines', name='Mean reversion strategy', line=dict(color='blue')))

fig.update_layout(title='Growth of $1 Investments',
                  xaxis=dict(title='Date'),
                  yaxis=dict(title='Cumulative Returns'),
                  legend=dict(orientation='h', yanchor='bottom', y=1.02, xanchor='right', x=1),
                  showlegend=True)
fig.show()

In [ ]:
print('Buy and hold strategy:',np.exp(df['Log_returns'].dropna()).cumprod()[-1]-1)
print('Mean reversion strategy:',np.exp(df['Strategy_returns'].dropna()).cumprod()[-1]-1)

Buy and hold strategy: 1.7940527008330882
Mean reversion strategy: 33.25265189493136


In [ ]:

position = 0  # 0: No position, 1: Short position, 2: Long position
initial_balance = 1000  # Initial balance in USDT
balance = initial_balance
trades = []


lookback_window = 13  # Number of periods to calculate the historical mean
entry_threshold = 2.0  # Entry threshold in standard deviations
exit_threshold = 0.5  # Exit threshold in standard deviations
stop_loss_percentage = 1.0

df['rolling_mean'] = df['Strategy_returns'].rolling(window=lookback_window).mean()
df['rolling_std'] = df['Strategy_returns'].rolling(window=lookback_window).std()

df['rolling_mean'] = df['rolling_mean'].fillna(method='bfill')
df['rolling_std'] = df['rolling_std'].fillna(method='bfill')


df['z_score'] = 0

for index, row in df.iterrows():
    if position == 0:
        rolling_std = max(1e-8, row['rolling_std'])
        df.at[index, 'z_score'] = (row['Strategy_returns'] - row['rolling_mean']) / rolling_std

        if df.at[index, 'z_score'] > entry_threshold:

            position = 1
            entry_price = row['close']
            position_size = balance / entry_price
            stop_loss_price = entry_price * (1 + stop_loss_percentage)
            balance -= position_size * entry_price
            trades.append(('Short', index, entry_price, position_size, stop_loss_price))

        elif df.at[index, 'z_score'] < -entry_threshold:

            position = 2
            entry_price = row['close']
            position_size = balance / entry_price
            stop_loss_price = entry_price * (1 - stop_loss_percentage)
            balance -= position_size * entry_price
            trades.append(('Long', index, entry_price, position_size, stop_loss_price))

    elif position == 1:
        rolling_std = max(1e-8, row['rolling_std'])
        df.at[index, 'z_score'] = (row['Strategy_returns'] - row['rolling_mean']) / rolling_std

        if row['close'] >= stop_loss_price:

            position = 0
            exit_price = row['close']
            balance += position_size * exit_price
            trades.append(('Cover', index, exit_price, position_size))

    elif position == 2:
        rolling_std = max(1e-8, row['rolling_std'])
        df.at[index, 'z_score'] = (row['Strategy_returns'] - row['rolling_mean']) / rolling_std

        if row['close'] <= stop_loss_price:

            position = 0
            exit_price = row['close']
            balance += position_size * exit_price
            trades.append(('Sell', index, exit_price, position_size))

# Calculate final balance
final_balance = balance + position_size * df['close'].iloc[-1] if position in [1, 2] else balance

# Calculate profits or losses
profit_loss = final_balance - initial_balance

# Display results
print(f"Initial Balance: {initial_balance} USDT")
print(f"Final Balance: {final_balance} USDT")
print(f"Profit/Loss: {profit_loss} USDT")

# Display trades
trades_df = pd.DataFrame(trades, columns=['Action', 'Date', 'Price', 'Size', 'Stop-Loss Price'])
print("\nTrades:")
print(trades_df)


Initial Balance: 1000 USDT
Final Balance: 2574.766044783639 USDT
Profit/Loss: 1574.7660447836388 USDT

Trades:
  Action                 Date     Price     Size  Stop-Loss Price
0  Short  2018-01-13 09:30:00  14255.09  0.07015         28510.18
1  Cover  2020-12-30 21:30:00  28776.46  0.07015              NaN
2   Long  2021-01-01 21:30:00  29029.04  0.06954             0.00


#**Model Building**

In [ ]:
pip install --upgrade xgboost

In [ ]:
from sklearn.model_selection import train_test_split
from xgboost import XGBRegressor
from sklearn.metrics import accuracy_score, mean_squared_error

In [ ]:
df['positions'] = pd.to_numeric(df['positions'], errors='coerce')
df['Buy'] = pd.to_numeric(df['Buy'], errors='coerce')
df['Sell'] = pd.to_numeric(df['Sell'], errors='coerce')

df.fillna(df.mean(), inplace=True)
X = df.drop(['Strategy_returns','ratios'], axis=1)
y = df['Strategy_returns'].fillna(0)
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.3, random_state=1)

model_mean_reversion = XGBRegressor(learning_rate=0.2, n_estimators=3000, max_depth=5, missing=np.nan)
model_mean_reversion.fit(X_train, y_train)



XGBRegressor(base_score=None, booster=None, callbacks=None,
             colsample_bylevel=None, colsample_bynode=None,
             colsample_bytree=None, device=None, early_stopping_rounds=None,
             enable_categorical=False, eval_metric=None, feature_types=None,
             gamma=None, grow_policy=None, importance_type=None,
             interaction_constraints=None, learning_rate=0.2, max_bin=None,
             max_cat_threshold=None, max_cat_to_onehot=None,
             max_delta_step=None, max_depth=5, max_leaves=None,
             min_child_weight=None, missing=nan, monotone_constraints=None,
             multi_strategy=None, n_estimators=3000, n_jobs=None,
             num_parallel_tree=None, random_state=None, ...)

In [ ]:
model_mean_reversion.score(X_train,y_train)

0.9967152672122043

In [ ]:
model_mean_reversion.score(X_test,y_test)

0.9825706850678768

In [ ]:
y_pred = model_mean_reversion.predict(X)

In [ ]:
signals = y_pred
returns = np.array(y)

if len(signals) != len(returns):
    returns = returns[:len(signals)]
    print("Returns trimmed to match the length of signals.")

position_returns = signals * returns

equity_curve = np.cumprod(1 + position_returns)

# Calculate the maximum drawdown
def calculate_drawdown(equity_curve):
    peak = np.maximum.accumulate(equity_curve)
    drawdown = (peak - equity_curve) / peak
    return drawdown

def calculate_max_drawdown(equity_curve):
    drawdown = calculate_drawdown(equity_curve)
    max_drawdown = np.max(drawdown)
    return max_drawdown

# Calculate the Sharpe ratio
def calculate_sharpe_ratio(returns):
    sharpe_ratio = np.mean(returns) / np.std(returns)
    return sharpe_ratio

# Print the results
print(f"Equity Curve: {equity_curve}")
print(f"Maximum Drawdown: {calculate_max_drawdown(equity_curve)}")
print(f"Sharpe Ratio: {calculate_sharpe_ratio(position_returns)}")


Equity Curve: [1.         1.         1.         ... 2.45018926 2.45056738 2.45094292]
Maximum Drawdown: 9.290846229106488e-06
Sharpe Ratio: 0.2843102459650479


In [ ]:
df['Predicted_Strategy_Returns'] = model_mean_reversion.predict(X)

position = 0
initial_balance = 1000
balance = initial_balance
trades = []

lookback_window = 19
entry_threshold = 4.0
exit_threshold = 0.5
stop_loss_percentage = 1.0

df['rolling_mean'] = df['Predicted_Strategy_Returns'].rolling(window=lookback_window).mean()
df['rolling_std'] = df['Predicted_Strategy_Returns'].rolling(window=lookback_window).std()

df['rolling_mean'] = df['rolling_mean'].fillna(method='bfill')
df['rolling_std'] = df['rolling_std'].fillna(method='bfill')

df['z_score'] = 0

for index, row in df.iterrows():
    if position == 0:
        rolling_std = max(1e-8, row['rolling_std'])
        df.at[index, 'z_score'] = (row['Predicted_Strategy_Returns'] - row['rolling_mean']) / rolling_std

        if df.at[index, 'z_score'] > entry_threshold:

            position = 1
            entry_price = row['close']
            position_size = balance / entry_price
            stop_loss_price = entry_price * (1 + stop_loss_percentage)
            balance -= position_size * entry_price
            trades.append(('Short', index, entry_price, position_size, stop_loss_price))

        elif df.at[index, 'z_score'] < -entry_threshold:

            position = 2
            entry_price = row['close']
            position_size = balance / entry_price
            stop_loss_price = entry_price * (1 - stop_loss_percentage)
            balance -= position_size * entry_price
            trades.append(('Long', index, entry_price, position_size, stop_loss_price))

    elif position == 1:
        rolling_std = max(1e-8, row['rolling_std'])
        df.at[index, 'z_score'] = (row['Predicted_Strategy_Returns'] - row['rolling_mean']) / rolling_std

        if row['close'] >= stop_loss_price:
            position = 0
            exit_price = row['close']
            balance += position_size * exit_price
            trades.append(('Cover', index, exit_price, position_size))

    elif position == 2:
        rolling_std = max(1e-8, row['rolling_std'])
        df.at[index, 'z_score'] = (row['Predicted_Strategy_Returns'] - row['rolling_mean']) / rolling_std

        if row['close'] <= stop_loss_price:
            position = 0
            exit_price = row['close']
            balance += position_size * exit_price
            trades.append(('Sell', index, exit_price, position_size))

final_balance = balance + position_size * df['close'].iloc[-1] if position in [1, 2] else balance

profit_loss = final_balance - initial_balance

print(f"Initial Balance: {initial_balance} USDT")
print(f"Final Balance: {final_balance} USDT")
print(f"Profit/Loss: {profit_loss} USDT")

trades_df = pd.DataFrame(trades, columns=['Action', 'Date', 'Price', 'Size', 'Stop-Loss Price'])
print("\nTrades:")
print(trades_df)

Initial Balance: 1000 USDT
Final Balance: 2157.607181209709 USDT
Profit/Loss: 1157.6071812097089 USDT

Trades:
  Action                 Date     Price      Size  Stop-Loss Price
0  Short  2018-01-13 09:30:00  14255.09  0.070150         28510.18
1  Cover  2020-12-30 21:30:00  28776.46  0.070150              NaN
2   Long  2021-07-04 05:30:00  34641.61  0.058273             0.00


#**Backtesting on Sample 1**

In [ ]:
new_df = pd.read_csv('/content/output 1.csv')

In [ ]:
new_df.columns

Index(['open', 'high', 'low', 'close', 'volume', 'SMA', 'Simple_returns',
       'Log_returns', 'ratios', 'positions', 'Buy', 'Sell', 'Strategy_returns',
       'rolling_mean', 'rolling_std', 'z_score'],
      dtype='object')

In [ ]:
from sklearn.metrics import mean_squared_error
X_new = new_df[['open', 'high', 'low', 'close', 'volume', 'SMA', 'Simple_returns',
       'Log_returns', 'positions', 'Buy', 'Sell',
       'rolling_mean', 'rolling_std', 'z_score']]
Y_new = new_df['Strategy_returns'].values

predicted_signals = model_mean_reversion.predict(X_new)

accuracy = mean_squared_error(Y_new, predicted_signals)

print("Model accuracy on new data:", accuracy)

Model accuracy on new data: 0.00033317006411690654


In [ ]:
mse_train = mean_squared_error(Y_new, predicted_signals)
mse_test = mean_squared_error(Y_new, predicted_signals)

print("Mean Squared Error on Training Set:", mse_train)
print("Mean Squared Error on Testing Set:", mse_test)

Mean Squared Error on Training Set: 0.00033317006411690654
Mean Squared Error on Testing Set: 0.00033317006411690654


In [ ]:
predicted_signals = model_mean_reversion.predict(X_new)
new_df['Predicted_Strategy_Returns'] = predicted_signals

position = 0
initial_balance = 1000
balance = initial_balance
trades = []


lookback_window = 19
entry_threshold = 4.0
exit_threshold = 0.5
stop_loss_percentage = 1.0


new_df['rolling_mean'] = new_df['Predicted_Strategy_Returns'].rolling(window=lookback_window).mean()
new_df['rolling_std'] = new_df['Predicted_Strategy_Returns'].rolling(window=lookback_window).std()

new_df['rolling_mean'] = new_df['rolling_mean'].fillna(method='bfill')
new_df['rolling_std'] = new_df['rolling_std'].fillna(method='bfill')

new_df['z_score'] = 0

for index, row in new_df.iterrows():
    if position == 0:
        rolling_std = max(1e-8, row['rolling_std'])
        new_df.at[index, 'z_score'] = (row['Predicted_Strategy_Returns'] - row['rolling_mean']) / rolling_std

        if new_df.at[index, 'z_score'] > entry_threshold:

            position = 1
            entry_price = row['close']
            position_size = balance / entry_price
            stop_loss_price = entry_price * (1 + stop_loss_percentage)
            balance -= position_size * entry_price
            trades.append(('Short', index, entry_price, position_size, stop_loss_price))

        elif new_df.at[index, 'z_score'] < -entry_threshold:

            position = 2
            entry_price = row['close']
            position_size = balance / entry_price
            stop_loss_price = entry_price * (1 - stop_loss_percentage)
            balance -= position_size * entry_price
            trades.append(('Long', index, entry_price, position_size, stop_loss_price))

    elif position == 1:
        rolling_std = max(1e-8, row['rolling_std'])
        new_df.at[index, 'z_score'] = (row['Predicted_Strategy_Returns'] - row['rolling_mean']) / rolling_std

        if row['close'] >= stop_loss_price or new_df.at[index, 'z_score'] < -exit_threshold:
            position = 0
            exit_price = row['close']
            balance += position_size * exit_price
            trades.append(('Cover', index, exit_price, position_size))

    elif position == 2:
        rolling_std = max(1e-8, row['rolling_std'])
        new_df.at[index, 'z_score'] = (row['Predicted_Strategy_Returns'] - row['rolling_mean']) / rolling_std

        if row['close'] <= stop_loss_price or new_df.at[index, 'z_score'] > exit_threshold:
            position = 0
            exit_price = row['close']
            balance += position_size * exit_price
            trades.append(('Sell', index, exit_price, position_size))

final_balance = balance + position_size * new_df['close'].iloc[-1] if position in [1, 2] else balance


profit_loss = final_balance - initial_balance


print(f"Initial Balance: {initial_balance} USDT")
print(f"Final Balance: {final_balance} USDT")
print(f"Profit/Loss: {profit_loss} USDT")

trades_df = pd.DataFrame(trades, columns=['Action', 'Date', 'Price', 'Size', 'Stop-Loss Price'])
print("\nTrades:")
print(trades_df)

Initial Balance: 1000 USDT
Final Balance: 1189.4784801006986 USDT
Profit/Loss: 189.47848010069856 USDT

Trades:
   Action  Date     Price         Size  Stop-Loss Price
0   Short    42  1.832314   545.757919         3.664628
1   Cover    43  1.721820   545.757919              NaN
2   Short   822 -0.677349 -1387.316110        -1.354697
3   Cover   823 -0.806919 -1387.316110              NaN
4    Long   865 -0.571749 -1957.944996        -0.000000
5    Sell   866 -0.603809 -1957.944996              NaN
6    Long   934 -0.683933 -1728.567585        -0.000000
7    Sell   935 -0.668768 -1728.567585              NaN
8    Long   978 -0.706408 -1636.462166        -0.000000
9    Sell   979 -0.733912 -1636.462166              NaN
10   Long  1084 -0.350862 -3423.052678        -0.000000
11   Sell  1085 -0.369375 -3423.052678              NaN
12  Short  1125 -0.384898 -3284.999547        -0.769796
13  Cover  1126 -0.379594 -3284.999547              NaN
14  Short  1239 -0.650183 -1917.868540        -1

In [ ]:
model_mean_reversion.score(X_new,Y_new)

0.6555356375748558

#**BackTesting on Sample 2**

In [ ]:
d = pd.read_csv('/content/output 2.csv')

In [ ]:
d.columns

Index(['open', 'high', 'low', 'close', 'volume', 'SMA', 'Simple_returns',
       'Log_returns', 'ratios', 'positions', 'Buy', 'Sell', 'Strategy_returns',
       'rolling_mean', 'rolling_std', 'z_score'],
      dtype='object')

In [ ]:
from sklearn.metrics import mean_squared_error
X_new = d[['open', 'high', 'low', 'close', 'volume', 'SMA', 'Simple_returns',
       'Log_returns', 'positions', 'Buy', 'Sell',
       'rolling_mean', 'rolling_std', 'z_score']]
Y_new = d['Strategy_returns'].values
predicted_signals = model_mean_reversion.predict(X_new)


accuracy = mean_squared_error(Y_new, predicted_signals)

print("Model accuracy on new data:", accuracy)

Model accuracy on new data: 0.001029316629918319


In [ ]:
predicted_signals = model_mean_reversion.predict(X_new)

d['Predicted_Strategy_Returns'] = predicted_signals

position = 0
initial_balance = 1000
balance = initial_balance
trades = []


lookback_window = 13
entry_threshold = 2.0
exit_threshold = 0.5
stop_loss_percentage = 1.0

d['rolling_mean'] = d['Predicted_Strategy_Returns'].rolling(window=lookback_window).mean()
d['rolling_std'] = d['Predicted_Strategy_Returns'].rolling(window=lookback_window).std()

d['rolling_mean'] = d['rolling_mean'].fillna(method='bfill')
d['rolling_std'] = d['rolling_std'].fillna(method='bfill')

d['z_score'] = 0

for index, row in d.iterrows():
    if position == 0:
        rolling_std = max(1e-8, row['rolling_std'])
        d.at[index, 'z_score'] = (row['Predicted_Strategy_Returns'] - row['rolling_mean']) / rolling_std

        if d.at[index, 'z_score'] > entry_threshold:
            position = 1
            entry_price = row['close']
            position_size = balance / entry_price
            stop_loss_price = entry_price * (1 + stop_loss_percentage)
            balance -= position_size * entry_price
            trades.append(('Short', index, entry_price, position_size, stop_loss_price))

        elif d.at[index, 'z_score'] < -entry_threshold:
            position = 2
            entry_price = row['close']
            position_size = balance / entry_price
            stop_loss_price = entry_price * (1 - stop_loss_percentage)
            balance -= position_size * entry_price
            trades.append(('Long', index, entry_price, position_size, stop_loss_price))

    elif position == 1:
        rolling_std = max(1e-8, row['rolling_std'])
        d.at[index, 'z_score'] = (row['Predicted_Strategy_Returns'] - row['rolling_mean']) / rolling_std

        if row['close'] >= stop_loss_price or d.at[index, 'z_score'] < -exit_threshold:
            position = 0
            exit_price = row['close']
            balance += position_size * exit_price
            trades.append(('Cover', index, exit_price, position_size))

    elif position == 2:
        rolling_std = max(1e-8, row['rolling_std'])
        d.at[index, 'z_score'] = (row['Predicted_Strategy_Returns'] - row['rolling_mean']) / rolling_std

        if row['close'] <= stop_loss_price or d.at[index, 'z_score'] > exit_threshold:
            position = 0
            exit_price = row['close']
            balance += position_size * exit_price
            trades.append(('Sell', index, exit_price, position_size))

final_balance = balance + position_size * d['close'].iloc[-1] if position in [1, 2] else balance

profit_loss = final_balance - initial_balance

print(f"Initial Balance: {initial_balance} USDT")
print(f"Final Balance: {final_balance} USDT")
print(f"Profit/Loss: {profit_loss} USDT")

trades_df = pd.DataFrame(trades, columns=['Action', 'Date', 'Price', 'Size', 'Stop-Loss Price'])
print("\nTrades:")
print(trades_df)

Initial Balance: 1000 USDT
Final Balance: -143.78174158927513 USDT
Profit/Loss: -1143.781741589275 USDT

Trades:
    Action  Date     Price        Size  Stop-Loss Price
0    Short     3 -2.231703 -448.088242        -4.463407
1    Cover     4 -2.230408 -448.088242              NaN
2     Long     9 -2.218854 -450.421438        -0.000000
3     Sell    10 -2.212303 -450.421438              NaN
4     Long    14 -2.183365 -456.391242        -0.000000
..     ...   ...       ...         ...              ...
116  Short  1283  0.491233  -73.198099         0.982467
117  Cover  1300  0.991708  -73.198099              NaN
118  Short  1310  1.296924  -55.971783         2.593849
119  Cover  1323  2.568825  -55.971783              NaN
120   Long  1325  2.568825  -55.971783         0.000000

[121 rows x 5 columns]
